In [ ]:
#Cleaning Raw Dataset
#Data Cleaning
import string
import numpy as np
import pandas as pd
import statistics as st
import pandas as pd
import csv
# Load imbd movies dataset
url = '/Users/rishikeshdhokare/Downloads/RawDataSet/movies.csv'
df = pd.read_csv(url)
poster_column = df.pop('Poster')  # Remove 'Poster' column from the DataFrame
df['Poster'] = poster_column
df = df.rename(columns={'Duration (min)': 'Duration'})
df = df.rename(columns={'Title': 'Title'})
df = df.drop_duplicates(subset=['Title'], keep='first')

# Example: Handling long text reviews
df['Review'] = df['Review'].apply(lambda x: str(x).replace("\n", " ")) 

df['Title'] = df['Title'].str.strip()

# Convert data types
df['Duration'] = pd.to_numeric(df['Duration'], errors='coerce')

# Standardize column names
df.columns = df.columns.str.replace(' ', '_')

# Filter data for valid durations
df = df[df['Duration'] > 0]  # Keep only movies with positive duration

# Display the cleaned DataFrame
print("Cleaned DataFrame:")
df
output_file = '/Users/rishikeshdhokare/Downloads/CleanDataset/movies.csv'
df.to_csv(output_file, quoting=csv.QUOTE_ALL, index=False)

In [ ]:
#Send parameter Title to the api and get data for different titles and create a new csv file

import pandas as pd
import requests
import time

# OMDb API settings
api_key = 'd84321b3'  # Replace with your actual API key
base_url_api = 'http://www.omdbapi.com/'

# Load the IMDb movies dataset
csv_file_path = '/Users/rishikeshdhokare/Downloads/RawDataSet/data.csv'
df = pd.read_csv(csv_file_path, encoding='ISO-8859-1')  # Specify encoding

# Extract movie titles from the DataFrame
movie_titles = df['Title'].tolist()  # Adjust the column name as necessary
# Initialize a list to store the fetched movie data
movies_data = []

# Iterate over each movie title in the list and fetch data from the OMDb API
for movie_title in movie_titles:
    params = {
        'apikey': api_key,
        't': movie_title
    }
    
    # Fetch data from OMDb API
    response = requests.get(base_url_api, params=params)

    # Print the status code for debugging
    print(f"Fetching data for: {movie_title}")
    print(f"Response Status Code: {response.status_code}")

    # Check if the response is valid JSON
    if response.status_code == 200:
        try:
            movie_data = response.json()
            # Check if the movie data is valid
            if movie_data.get('Response') == 'True':
                # Append relevant data to the movies_data list
                movies_data.append({
                    'Title': movie_data.get('Title', None),
                    'Year': movie_data.get('Year', None),
                    'Rated': movie_data.get('Rated', None),
                    'Genre': movie_data.get('Genre', None),
                    'Runtime': movie_data.get('Runtime', None),
                    'Plot': movie_data.get('Plot', None),
                    'Actors': movie_data.get('Actors', None),
                    'Metascore': movie_data.get('Metascore', None),
                    'Director': movie_data.get('Director', None),
                    'imdbRating': movie_data.get('imdbRating', None),
                    'imdbVotes': movie_data.get('imdbVotes', None),
                    'Awards': movie_data.get('Awards', None),
                    'Country': movie_data.get('Country', None),
                    'Language': movie_data.get('Language', None),
                    'BoxOffice': movie_data.get('BoxOffice', None)
                })
            else:
                print(f"Error fetching data for '{movie_title}': {movie_data.get('Error')}")
        except ValueError:
            print(f"Error decoding JSON for {movie_title}: {response.text}")
    else:
        print(f"Error: Received status code {response.status_code} for '{movie_title}'")
        print("Response text:", response.text)

    time.sleep(2)  

# Convert the list of dictionaries into a DataFrame
api_movies_df = pd.DataFrame(movies_data)

# Check if 'Title' exists in both DataFrames
if 'Title' in df.columns and 'Title' in api_movies_df.columns:
    merged_df = pd.merge(df, api_movies_df, on='Title', how='outer')  # 'outer' if you want to keep all titles
    print("Merged DataFrame:")
    print(merged_df)
    
    merged_df.to_csv('/Users/rishikeshdhokare/Downloads/CleanDataset/000_cleaned_movies_data.csv', index=False)
else:
    print("Error: 'Title' column is missing in one of the DataFrames.")


In [ ]:
# Merge all the api generated files
import pandas as pd

# Load both CSV files into DataFrames
df1 = pd.read_csv('/Users/rishikeshdhokare/Downloads/MergedDataSet/ToClean/14.csv')
df2 = pd.read_csv('/Users/rishikeshdhokare/Downloads/MergedDataSet/Cleaned/merged_file.csv')

# Concatenate the DataFrames row-wise
merged_df = pd.concat([df1, df2], ignore_index=True)

# Save the combined DataFrame to a new CSV file (optional)
merged_df.to_csv('/Users/rishikeshdhokare/Downloads/MergedDataSet/Cleaned/final_merged_file.csv', index=False)

# Print the merged DataFrame
print(merged_df)

In [74]:
import pandas as pd
import requests
import time

# Your OMDB API key
api_key = '2f6045c4'

# Load the unknowns dataset
unknowns_df = pd.read_csv('/Users/rishikeshdhokare/Downloads/MergedDataSet/Cleaned/unknowns.csv')

# Function to get runtime from OMDB API
def get_runtime_from_omdb(title):
    try:
        # Construct the API URL with the title and your API key
        url = f"http://www.omdbapi.com/?t={title}&apikey={api_key}"
        response = requests.get(url)
        data = response.json()
        # Print the status code for debugging
        print(f"Fetching data for: {data}")
        print(f"Response Status Code: {response.status_code}")
        # Check if the response is valid
        if data.get('Response') == 'True':
            return data.get('Runtime')  # Returns runtime (e.g., '103 min')
        else:
            print(f"Title '{title}' not found.")
            return None
    except Exception as e:
        print(f"Error fetching data for {title}: {e}")
        return None

# Iterate over titles in the unknowns DataFrame
unknowns_df['Runtime'] = unknowns_df['Title'].apply(get_runtime_from_omdb)

# Save the updated DataFrame with the fetched runtime
unknowns_df.to_csv('/Users/rishikeshdhokare/Downloads/MergedDataSet/Cleaned/updated_unknowns.csv', index=False)

# Show the first few rows of the updated DataFrame
print(unknowns_df.head())


Fetching data for: {'Title': 'AVP: Alien vs. Predator - FX Special Event', 'Year': '2005', 'Rated': 'N/A', 'Released': '19 Jan 2005', 'Runtime': 'N/A', 'Genre': 'N/A', 'Director': 'Joseph Arnao', 'Writer': 'N/A', 'Actors': 'Jennifer Lothrop, Dave Holmes', 'Plot': 'N/A', 'Language': 'English', 'Country': 'United States', 'Awards': 'N/A', 'Poster': 'N/A', 'Ratings': [{'Source': 'Internet Movie Database', 'Value': '6.6/10'}], 'Metascore': 'N/A', 'imdbRating': '6.6', 'imdbVotes': '36', 'imdbID': 'tt0472993', 'Type': 'movie', 'DVD': 'N/A', 'BoxOffice': 'N/A', 'Production': 'N/A', 'Website': 'N/A', 'Response': 'True'}
Response Status Code: 200
Fetching data for: {'Title': 'Amoureux de la pianiste', 'Year': '1913', 'Rated': 'N/A', 'Released': 'N/A', 'Runtime': 'N/A', 'Genre': 'Short', 'Director': 'N/A', 'Writer': 'N/A', 'Actors': 'N/A', 'Plot': 'N/A', 'Language': 'None, French', 'Country': 'France', 'Awards': 'N/A', 'Poster': 'N/A', 'Ratings': [], 'Metascore': 'N/A', 'imdbRating': 'N/A', 'imd

In [ ]:
import pandas as pd

# Load your data file and API file
data_file_path = '/Users/rishikeshdhokare/Downloads/MergedDataSet/ToClean/movies.csv'
api_file_path = '/Users/rishikeshdhokare/Downloads/MergedDataSet/Cleaned/merged_file.csv'

df_data = pd.read_csv(data_file_path)
df_api = pd.read_csv(api_file_path)

# Display the first few rows of both DataFrames for reference
print("Data File:")
print(df_data.head())
print("\nAPI File:")
print(df_api.head())

# Get unique genres from the data file
data_genres = set(df_data['Genre'].unique())

# Create a mask for rows in the API file that match the genres from the data file
mask = df_api['Genre'].isin(data_genres)

# Create a new DataFrame that keeps only the matching genres in the Genre column
result_df = df_api.copy()  # Start with a copy of the API DataFrame
result_df.loc[~mask, 'Genre'] = None  # Set genres that do not match to None

# Identify rows with NaN in the Genre column
nan_mask = result_df['Genre'].isna()

# Merge the API DataFrame with the data DataFrame on Title
merged_df = result_df.merge(df_data[['Title', 'Genre']], on='Title', how='left', suffixes=('', '_data'))

# Fill NaN values in Genre with corresponding Genre from data file
merged_df['Genre'] = merged_df['Genre'].fillna(merged_df['Genre_data'])

# Drop the auxiliary Genre_data column
merged_df.drop(columns=['Genre_data'], inplace=True)

# Optionally: Resetting the index if needed
merged_df.reset_index(drop=True, inplace=True)

# Display the result
print("\nResult DataFrame:")
print(merged_df.head())

# Save the resulting DataFrame to a CSV file
merged_df.to_csv('/Users/rishikeshdhokare/Downloads/MergedDataSet/Cleaned/merged_file_genre_filled.csv', index=False)


In [96]:
import pandas as pd
import requests
import time
import csv
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
# Load imbd movies dataset
url = '/Users/rishikeshdhokare/Downloads/MergedDataSet/Cleaned/final_merged_file.csv'
df = pd.read_csv(url)

######### Year column #########
df['Year_y'] = np.where(df['Year_y'].isnull(), df['Year_x'], df['Year_y'])
df.drop('Year_x', axis=1, inplace=True)

######### Year column #########
# Merge Genre_x and Genre_y into a new column called 'Genre'
df['Genre'] = df['Genre_x'].fillna('') + df['Genre_y'].fillna('')
df['Genre'] = df['Genre'].str.strip()

df.drop('Genre_x', axis=1, inplace=True)
df.drop('Genre_y', axis=1, inplace=True)

######### Metascore column #########
df['Metascore_y'] = df['Metascore_y'].fillna(df['Metascore_x'])
df.drop(columns=['Metascore_x'], inplace=True)
df.rename(columns={'Metascore_y': 'Metascore'}, inplace=True)

######### Metascore column #########
df['Director_y'] = df['Director_y'].fillna(df['Director_x'])
df.drop(columns=['Director_x'], inplace=True)
df.rename(columns={'Director_y': 'Director'}, inplace=True)

df.columns = df.columns.str.replace(r'(_x_x|_x_y|_x|_y)$', '', regex=True)

######### imdbRating column #########
# Replace null values in 'imdbRating' with values from 'Rating'
df['imdbRating'] = df['imdbRating'].fillna(df['Rating'])
df.drop(columns=['Rating'], inplace=True)

######### Cast column #########
df['Cast'] = df['Cast'].fillna(df['Actors'])
df.drop('Actors', axis=1, inplace=True)
df.rename(columns={'Cast': 'Actor'}, inplace=True)

# Drop rows where 'BoxOffice' is NaN or empty
df = df.dropna(subset=['BoxOffice'])
df = df[df['BoxOffice'] != '']

#drop columns 
df.drop('Review Count', axis=1, inplace=True)
df.drop('Review Title', axis=1, inplace=True)
df.drop('Duration', axis=1, inplace=True)
df.drop('Metascore', axis=1, inplace=True)
df.drop('Review_Title', axis=1, inplace=True)
df.drop('Review_Count', axis=1, inplace=True)
df.drop('Review', axis=1, inplace=True)
df.drop('Description', axis=1, inplace=True)
df.drop('Poster', axis=1, inplace=True)
df.drop('Plot', axis=1, inplace=True)
df.drop('Certificate', axis=1, inplace=True)
df.drop('Votes', axis=1, inplace=True)
df.drop('Rated', axis=1, inplace=True)
df.drop('Director', axis=1, inplace=True)

# Replace 'Ã' with an empty string or appropriate character
df.replace({'ÃÂ': ''}, regex=True, inplace=True)

###Remove limits in columns and rows display###
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
df.head()

# Reorder columns: Move specified columns to the front
new_order = ['Title', 'Actor', 'Genre', 'imdbRating', 'imdbVotes', 'Runtime','BoxOffice', 'Year'] + [col for col in df.columns if col not in ['Title', 'Actor', 'Genre', 'imdbRating', 'imdbVotes','Runtime', 'BoxOffice', 'Year']]
df = df[new_order]

# Save the updated DataFrame with the fetched runtime
df.to_csv('/Users/rishikeshdhokare/Downloads/MergedDataSet/Cleaned/final_merged_file1.csv', index=False)

In [162]:
import pandas as pd

# Load your dataset
df = pd.read_csv('/Users/rishikeshdhokare/Downloads/MergedDataSet/Final/final_omdb_data1.csv')
df.drop('Classification', axis=1, inplace=True)
df.columns
df.to_csv('/Users/rishikeshdhokare/Downloads/MergedDataSet/Final/final_omdb_data.csv', index=False)
df

Title  \
0                                               Gattaca   
1                                           Io Capitano   
2                              The Light Between Oceans   
3                                         28 Days Later   
4                                     F9: The Fast Saga   
5                             GHOST: Rite Here Rite Now   
6          Harry Potter and the Deathly Hallows: Part 1   
7          Harry Potter and the Deathly Hallows: Part 2   
8                                            La Chimera   
9                           Mad Max 2: The Road Warrior   
10                 Mission: Impossible - Ghost Protocol   
11                         Rogue One: A Star Wars Story   
12                   Star Wars: Episode IV - A New Hope   
13                               The 40-Year-Old Virgin   
14                                     X2: X-Men United   
15                                                Blade   
16                                        Belle de Jour   
17                                   Huo guo ying xiong   
18                   Tenacious D in the Pick of Destiny   
19                                  And Justice for All   
20                                          El Mariachi   
21                   Star Wars: Episode IV - A New Hope   
22    The Chronicles of Narnia: The Lion, the Witch ...   
23            Three Billboards Outside Ebbing, Missouri   
24       Wallace & Gromit: The Curse of the Were-Rabbit   
25                        What's Love Got to Do with It   
26                                           Entre Nous   
27    Jeanne Dielman, 23, quai du commerce, 1080 Bru...   
28                             No Retreat, No Surrender   
29                                            Rocketman   
30                                             The DUFF   
31                                 The Snowtown Murders   
32                      The Wind that Shakes the Barley   
33                                    Ju-on: The Grudge   
34           The NeverEnding Story II: The Next Chapter   
35                                Au Revoir les Enfants   
36                        Disappearance at Clifton Hill   
37                       Goliyon Ki Raasleela Ram Leela   
38                                  Hiroshima Mon Amour   
39                                 Hot Dog... The Movie   
40               Little Nemo: Adventures in Slumberland   
41                                                Shoah   
42                                             SubUrbia   
43                                             SuperFly   
44                                    Waking Ned Devine   
45                            Ong-Bak: The Thai Warrior   
46                                     About Last Night   
47                                                 Lola   
48                                            Fired Up!   
49                        Teen Titans GO! To the Movies   
50                         Welcome Home, Roscoe Jenkins   
51                                        Che: Part One   
52                                  Herbie Fully Loaded   
53                                        Amores Perros   
54                               Green Street Hooligans   
55                                       The Aristocats   
56                                              Gattaca   
57                                          Io Capitano   
58                             The Light Between Oceans   
59                                  10 Cloverfield Lane   
60                                           12 Monkeys   
61                                     12 Years a Slave   
62                                       13 Going on 30   
63            13 Hours: The Secret Soldiers of Benghazi   
64                                             17 Again   
65                                     2 Fast 2 Furious   
66                                             3 Ninjas   
67                               300: 

In [ ]:
import pandas as pd

# Load your dataset
df = pd.read_csv('/Users/rishikeshdhokare/Downloads/MergedDataSet/Cleaned/merged_file_genre_filled.csv')

# Function to extract runtime in minutes from the string
def extract_runtime(runtime_str):
    if isinstance(runtime_str, str):
        # Extract the numeric part of the runtime
        return int(runtime_str.split()[0])  # Convert to int
    return None

# Function to classify by runtime
def classify_by_runtime(runtime):
    if pd.isna(runtime):
        return 'Unknown'
    
    # Classify based on typical ranges
    if 60 <= runtime <= 300:
        return 'Movie'
    elif 20 <= runtime < 60:
        return 'Series'
    else:
        return 'Unknown'

# Extract runtime in minutes and create a new column
df['Runtime'] = df['Runtime'].apply(extract_runtime)

# Classify based on runtime
df['Type'] = df['Runtime'].apply(classify_by_runtime)

# Display the updated DataFrame with relevant columns
print(df[['Title', 'Runtime', 'Type']])

movies = df[df['Type'] == 'Movie']
series = df[df['Type'] == 'Series']
unknowns = df[df['Type'] == 'Unknown']

# Print counts for diagnosis
print(f"\nNumber of Movies: {len(movies)}")
print(f"Number of Series: {len(series)}")
print(f"Number of Unknowns: {len(unknowns)}")

# Save the filtered results
#movies.to_csv('/Users/rishikeshdhokare/Downloads/MergedDataSet/Cleaned/movies.csv', index=False)
#series.to_csv('/Users/rishikeshdhokare/Downloads/MergedDataSet/Cleaned/series.csv', index=False)
#unknowns.to_csv('/Users/rishikeshdhokare/Downloads/MergedDataSet/Cleaned/unknowns.csv', index=False)

df.to_csv('/Users/rishikeshdhokare/Downloads/MergedDataSet/Cleaned/final_omdb_data.csv', index=False)

In [182]:
import pandas as pd
import re
# Load imbd movies dataset
url = '/Users/rishikeshdhokare/Downloads/MergedDataSet/Final/movies_no_duplicates.csv'
df = pd.read_csv(url)

# Remove duplicate rows based on the 'Title' column, keeping the first occurrence
df_no_duplicates = df.drop_duplicates(subset='Title', keep='first')

# Display the result to verify
print("DataFrame after removing duplicates:")
print(df_no_duplicates[['Title']].head())

# Function to check if a title contains only numbers or special characters (no alphabets)
def is_only_numbers_or_special_chars(title):
    # Regex to check if the title does NOT contain any alphabetic characters (only numbers and special characters)
    return bool(re.match(r'^[^a-zA-Z]+$', title))

# Apply the function to filter out titles that match the condition
df_cleaned = df[~df['Title'].apply(is_only_numbers_or_special_chars)]

# Function to standardize documentary genres
def standardize_documentry_genres(genre):
    if isinstance(genre, str):
        # Replace specific documentary genres with 'Documentary'
        if 'Documentary' in genre:
            return 'Documentary'
    return genre

# Apply the function to the 'Genre' column
df['Genre'] = df['Genre'].apply(standardize_documentry_genres)

# Function to standardize animation genres
def standardize_animation_genres(genre):
    if isinstance(genre, str):
        # Replace specific animation genres with 'Animation'
        if 'Animation' in genre:
            return 'Animation'
    return genre

# Apply the function to the 'Genre' column
df['Genre'] = df['Genre'].apply(standardize_animation_genres)

# Function to standardize animation genres
def standardize_biography_genres(genre):
    if isinstance(genre, str):
        # Replace specific animation genres with 'Animation'
        if 'Biography' in genre:
            return 'Biography'
    return genre

# Apply the function to the 'Genre' column
df['Genre'] = df['Genre'].apply(standardize_biography_genres)

# Function to standardize animation genres
def standardize_adventure_genres(genre):
    if isinstance(genre, str):
        # Replace specific animation genres with 'Animation'
        if 'Adventure' in genre:
            return 'Adventure'
    return genre

# Apply the function to the 'Genre' column
df['Genre'] = df['Genre'].apply(standardize_adventure_genres)

# Replace "Musical" with "Music" in the Genre column
df['Genre'] = df['Genre'].str.replace('Musical', 'Music', regex=False)

# Select titles where the Genre contains 'Music'
df_music = df[df['Genre'].str.contains('Music', na=False)]

# Function to check if a title contains only numbers or special characters (no alphabets)
def is_only_numbers_or_special_chars(title):
    # Regex to check if the title does NOT contain any alphabetic characters (only numbers and special characters)
    return bool(re.match(r'^[^a-zA-Z]+$', title))

# Apply the function to filter out titles that match the condition
df_cleaned = df[~df['Title'].apply(is_only_numbers_or_special_chars)]

df_cleaned.to_csv('/Users/rishikeshdhokare/Downloads/MergedDataSet/Final/final_omdb_data_no_duplicates.csv', index=False)

DataFrame after removing duplicates:
                        Title
0                         '71
1     *batteries not included
2                          10
3         10 Cloverfield Lane
4  10 Things I Hate About You
